# Phase

Understanding phase is crucial in audio engineering and acoustics, especially when working with multiple microphones, speakers, or tracks, as incorrect phase relationships can result in unwanted coloration or loss of sound.

Phase describes the position of a point within a single cycle of a periodic waveform, like a sound wave. 

:::{note}
For audio signals, phase is measured as an angle (in degrees or radians), often relative to another signal or a fixed reference point.
:::

In [3]:
import numpy as np
import plotly.graph_objects as go

# Time axis: show two cycles of a 2 Hz tone sampled at 1 kHz
fs = 1_000
frequency = 2  # Hz
t = np.linspace(0, 2 / frequency, int(2 * fs / frequency))

reference = np.sin(2 * np.pi * frequency * t)
phase_shift_deg = 90  # shift by one quarter of a cycle
shifted = np.sin(2 * np.pi * frequency * t + np.deg2rad(phase_shift_deg))

fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=t,
        y=reference,
        name="Reference (0° phase)",
        line=dict(color="#1f77b4"),
    )
)
fig.add_trace(
    go.Scatter(
        x=t,
        y=shifted,
        name=f"Shifted (+{phase_shift_deg}°)",
        line=dict(color="#ff7f0e"),
    )
)

fig.update_layout(
    title=dict(
        text="Phase Shift Between Two Sine Waves",
        y=0.92,
        x=0.5,
        xanchor="center",
        pad=dict(t=40),
    ),
    xaxis_title="Time (seconds)",
    yaxis_title="Amplitude",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    margin=dict(l=40, r=20, t=120, b=40),
    template="plotly_white",
    annotations=[
        dict(
            x=t[int(len(t) * 0.15)],
            y=shifted[int(len(t) * 0.15)],
            text="Phase shift causes peaks to move",
            showarrow=True,
            arrowhead=2,
            ax=40,
            ay=-30,
        ),
    ],
)

fig.show()


## Degrees and Radians

Phase can be expressed in **degrees** (°) or **radians** (rad). Both units describe the same concept — how far one wave is shifted relative to another—but use different measurement systems:

- **Degrees** divide a full cycle into 360 equal parts. For example, 90° is one quarter of a wave cycle, 180° is half a cycle.
- **Radians** divide a full cycle into $2\pi$ parts: $2\pi$ radians equals 360°. Thus, 1 radian is about 57.3°, and a phase shift of  $\pi$ radians is equivalent to 180°.

Both units are interchangeable:
$$
  \text{Radians} = \frac{\pi}{180} \times \text{Degrees}
$$
$$
  \text{Degrees} = \frac{180}{\pi} \times \text{Radians}
$$

:::{note}
In mathematical formulas, radians are commonly used, especially in programming and signal processing, because many trigonometric functions expect angles in radians. However, degrees are often preferred in everyday language for their intuitive feel.
:::

In [4]:
import numpy as np
import plotly.graph_objects as go

def deg_to_rad(deg):
    return np.deg2rad(deg)
def rad_to_deg(rad):
    return np.rad2deg(rad)

theta = np.linspace(0, 2 * np.pi, 400)

def make_unit_circle_trace(degrees):
    radians = deg_to_rad(degrees)
    # Arc for selected phase
    angle_arc = np.linspace(0, radians, 100)
    x_arc = np.cos(angle_arc)
    y_arc = np.sin(angle_arc)

    traces = []

    # Draw the unit circle
    traces.append(go.Scatter(
        x=np.cos(theta), y=np.sin(theta),
        mode='lines',
        name='Unit Circle',
        line=dict(color="#888", dash='dot'),
        showlegend=False
    ))

    # Draw the angle arc
    traces.append(go.Scatter(
        x=np.concatenate(([1], x_arc)),
        y=np.concatenate(([0], y_arc)),
        fill='tozeroy',
        mode="lines", 
        name="Angle Arc",
        line=dict(width=4, color="#1f77b4"),
        opacity=0.7,
        showlegend=False
    ))

    # Draw marker at arc tip
    traces.append(go.Scatter(
        x=[np.cos(radians)], y=[np.sin(radians)],
        mode='markers',
        marker=dict(size=18, color="#d62728"),
        showlegend=False
    ))

    return traces

# Create plotly FigureWidget with slider
degrees_range = np.arange(0, 361, 1)
init_degrees = 90

# Prepare frames for animation (for smooth slider update)
frames = []
for deg in degrees_range:
    radians = deg_to_rad(deg)
    frames.append(
        go.Frame(
            data=make_unit_circle_trace(deg),
            name=str(deg),
            layout=go.Layout(
                title=dict(
                    text=f"Angle: {deg}° = {radians:.2f} radians",
                    x=0.5, xanchor="center", y=0.89, yanchor="top"
                )
            )
        )
    )

# Prepare initial traces
init_traces = make_unit_circle_trace(init_degrees)
init_radians = deg_to_rad(init_degrees)

fig = go.Figure(
    data=init_traces,
    layout=go.Layout(
        template="plotly_white",
        xaxis=dict(
            scaleanchor="y", scaleratio=1, showgrid=False, zeroline=False, visible=False,
            range=[-1.1, 1.1]
        ),
        yaxis=dict(
            showgrid=False, zeroline=False, visible=False,
            range=[-1.1, 1.1]
        ),
        title=dict(
            text=f"Angle: {init_degrees}° = {init_radians:.2f} radians",
            x=0.5, xanchor="center", y=0.89, yanchor="top"
        ),
        margin=dict(l=30, r=30, t=60, b=30),

        sliders=[{
            "steps": [
                {
                    "args": [
                        [str(deg)],
                        {
                            "frame": {"duration": 0, "redraw": True},
                            "mode": "immediate",
                            "transition": {"duration": 0}
                        }
                    ],
                    "label": str(deg) + "°",
                    "method": "animate"
                } for deg in degrees_range
            ],
            "active": init_degrees,
            "currentvalue": {"prefix": "Phase (°): "},
            "pad": {"t": 35},
            "len": 0.8,
            "x": 0.1,
            "y": -0.08,
        }],
    ),
    frames=frames
)

fig.show()

## Constructive and Destructive Interference

When two or more audio signals of the same frequency are combined, their phase relationship can lead to constructive interference (increasing amplitude) or destructive interference (decreasing or cancelling amplitude). For instance, if two identical sine waves are perfectly in phase (their peaks and troughs align), they add up to a larger wave. If they are 180 degrees out of phase (one's peak aligns with the other's trough), they can cancel each other out.

```{warning} Phase is Frequency Dependent
Remember that phase is always defined *relative to frequency*. A phase shift of a given number of degrees (or radians) corresponds to a different time shift depending on the frequency of the wave. For example, a 90° phase shift at 1 Hz is a very different time offset than a 90° phase shift at 1000 Hz. Always consider the frequency when interpreting or applying phase shifts!
```

In [5]:
import numpy as np
import plotly.graph_objects as go

# Interactive visualization of constructive vs destructive interference
fs = 1_000
frequency = 4  # Hz
t = np.linspace(0, 2 / frequency, int(2 * fs / frequency))
omega = 2 * np.pi * frequency

fixed_wave = np.sin(omega * t)

phase_values = np.arange(0, 361, 15)


def interference_label(phase):
    phase = phase % 360
    if phase in (0, 360):
        return "Constructive (maximum amplitude)"
    if phase == 180:
        return "Destructive (cancellation)"
    if 0 < phase < 180:
        return "Mostly constructive"
    return "Mostly destructive"


fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=t,
        y=fixed_wave,
        name="Wave 1 (reference)",
        line=dict(color="#1f77b4"),
    )
)
initial_phase = phase_values[0]
initial_wave = np.sin(omega * t + np.deg2rad(initial_phase))
fig.add_trace(
    go.Scatter(
        x=t,
        y=initial_wave,
        name=f"Wave 2 (+{initial_phase}°)",
        line=dict(color="#ff7f0e"),
    )
)
fig.add_trace(
    go.Scatter(
        x=t,
        y=fixed_wave + initial_wave,
        name="Sum (Wave 1 + Wave 2)",
        line=dict(color="#2ca02c", width=3),
    )
)

frames = []
for phase in phase_values:
    shifted_wave = np.sin(omega * t + np.deg2rad(phase))
    combined = fixed_wave + shifted_wave
    frames.append(
        go.Frame(
            name=str(phase),
            data=[
                go.Scatter(y=fixed_wave),
                go.Scatter(y=shifted_wave, name=f"Wave 2 (+{phase}°)"),
                go.Scatter(y=combined),
            ],
            layout=go.Layout(
                title=dict(
                    text=f"Phase difference: {phase}° — {interference_label(phase)}",
                    y=0.92,
                    pad=dict(t=40),
                )
            ),
        )
    )

fig.frames = frames

slider_steps = []
for phase in phase_values:
    slider_steps.append(
        dict(
            args=[
                [str(phase)],
                {
                    "frame": {"duration": 0, "redraw": True},
                    "mode": "immediate",
                    "transition": {"duration": 0},
                },
            ],
            label=f"{phase}°",
            method="animate",
        )
    )

fig.update_layout(
    height=600,
    title=dict(
        text=f"Phase difference: {initial_phase}° — {interference_label(initial_phase)}",
        y=0.92,
        x=0.5,
        xanchor="center",
        pad=dict(t=40),
    ),
    xaxis_title="Time (seconds)",
    yaxis_title="Amplitude",
    margin=dict(l=40, r=20, t=140, b=40),
    template="plotly_white",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    sliders=[
        dict(
            active=0,
            currentvalue=dict(prefix="Phase difference: "),
            pad=dict(t=80),
            steps=slider_steps,
        )
    ],
)

fig.show()



```{hint}
Use the above slider the interactive plot to adjust the phase difference between two sine waves.
This lets you see how changing phase affects their combination — observe how the resulting waveform changes as you move the slider.
```

## Listen to Phase Shift

In the interactive widget below, you can listen to how changing the phase shift between two sine waves alters what you hear. Move the "Phase shift" slider to adjust the phase difference, and notice how the combined sound changes depending on the amount of phase shift. This helps illustrate how phase relationships between sounds affect their acoustic result, especially in terms of constructive and destructive interference.

:::{hint}

**Want to interact with the audio widget in your browser?**

You can launch this notebook on [Binder](https://mybinder.org/) to play with the phase shift slider and listen to the audio output live, right in your web browser.

**How to do it:**
1. Click the "Rocket" or "Binder" badge at the top of this notebook (or visit [mybinder.org](https://mybinder.org/)).
2. Paste the GitHub repository URL for this project into Binder, or use any provided launch link.
3. Once the environment loads, navigate to this notebook file.
4. Move the "Phase shift" slider to change the phase difference between the two waves and press the play button to listen.

:::

In [6]:
from IPython.display import Audio, display
import ipywidgets as widgets

fs_audio = 44_100
frequency_audio = 440
duration = 2.0

time_audio = np.linspace(0, duration, int(fs_audio * duration), endpoint=False)
reference_audio = np.sin(2 * np.pi * frequency_audio * time_audio)

phase_slider = widgets.IntSlider(
    value=0,
    min=0,
    max=360,
    step=15,
    description="Phase shift",
    continuous_update=False,
    layout=widgets.Layout(width="400px"),
)

info_html = widgets.HTML()
audio_output = widgets.Output()


controls = widgets.VBox([phase_slider, info_html, audio_output])
display(controls)


def update_audio(phase_deg):
    shifted = np.sin(2 * np.pi * frequency_audio * time_audio + np.deg2rad(phase_deg))
    summary = reference_audio + shifted
    max_abs = np.max(np.abs(summary))
    if max_abs > 0:
        summary = summary / max_abs

    label = interference_label(phase_deg)
    info_html.value = f"<b>Phase:</b> {phase_deg}° — {label}"

    with audio_output:
        audio_output.clear_output(wait=True)
        display(Audio(summary, rate=fs_audio, autoplay=False))


interactive_widget = widgets.interactive_output(update_audio, {"phase_deg": phase_slider})
